In [209]:
import geopandas
import folium
import fiona
import pandas
fiona.drvsupport.supported_drivers['libkml'] = 'rw' 
fiona.drvsupport.supported_drivers['LIBKML'] = 'rw' 

In [210]:
df = geopandas.read_file("EWR Alignment Ox2CamSouth ln.shp")
print(df)

   objectid name    st_length_  \
0         1  CS3  65926.744941   
1         2  CS2  27395.409475   
2         3  CS1  50417.735543   

                                            geometry  
0  MULTILINESTRING Z ((544377.408 251506.330 0.00...  
1  LINESTRING Z (486936.480 233752.200 0.000, 486...  
2  MULTILINESTRING Z ((468677.990 225730.870 0.00...  


In [211]:
bfare = geopandas.read_file(r'/home/jonititan/Projects/DataExploration/EWR/pn_20230727_BFARe.kml')
print(bfare)
print(list(bfare))
bfaregroups = pandas.read_csv(r'/home/jonititan/Projects/DataExploration/EWR/bfareGroups.csv',index_col=0)
bfare['group'] = bfaregroups['group']


                                        Name  description timestamp begin end  \
0                                        MML          NaN       NaT   NaT NaT   
1                                        MVL          NaN       NaT   NaT NaT   
2                                       ECML          NaN       NaT   NaT NaT   
3                  Bromham Bridge - Sect C/D          NaN       NaT   NaT NaT   
4            Clapham Green (Start of Sect D)          NaN       NaT   NaT NaT   
5                                Alignment 1          NaN       NaT   NaT NaT   
6             Original RA1 Wilden - Colesden          NaN       NaT   NaT NaT   
7                                Alignment 2          NaN       NaT   NaT NaT   
8                                Alignment 6          NaN       NaT   NaT NaT   
9                                Alignment 8          NaN       NaT   NaT NaT   
10                               Alignment 9          NaN       NaT   NaT NaT   
11                         A

In [212]:
import random 
colours_to_choose_from = ['red', 'blue', 'green', 'purple', 'orange', 'darkred',
                'lightred', 'darkblue', 'darkgreen', 'cadetblue',
                'darkpurple', 'pink', 'lightblue', 'lightgreen',
                'gray']
random.shuffle(colours_to_choose_from)
colordict={a:colours_to_choose_from.pop() for a in bfare['group'].unique()}
bfare['color'] = bfare.apply(lambda r: colordict[r['group']],axis=1)

In [213]:
df.crs

In [214]:
from pyproj import CRS

In [215]:
crs = CRS('EPSG:27700')

In [216]:
df.crs = crs

In [217]:
df.to_crs("EPSG:4326",inplace=True)

In [218]:
df = df.explode(index_parts=True)
df.reset_index(inplace=True)
print(df)

   level_0  level_1  objectid name    st_length_  \
0        0        0         1  CS3  65926.744941   
1        0        1         1  CS3  65926.744941   
2        0        2         1  CS3  65926.744941   
3        0        3         1  CS3  65926.744941   
4        1        0         2  CS2  27395.409475   
5        2        0         3  CS1  50417.735543   
6        2        1         3  CS1  50417.735543   

                                            geometry  
0  LINESTRING Z (0.10847 52.14300 0.00000, 0.1067...  
1  LINESTRING Z (0.10847 52.14300 0.00000, 0.1111...  
2  LINESTRING Z (-0.48467 52.14112 0.00000, -0.48...  
3  LINESTRING Z (-0.48422 52.15685 47.99900, -0.4...  
4  LINESTRING Z (-0.73517 51.99543 0.00000, -0.73...  
5  LINESTRING Z (-1.00265 51.92588 0.00000, -0.99...  
6  LINESTRING Z (-1.00266 51.92588 0.00000, -1.01...  


In [219]:
waywidth = df.copy()
waywidth.to_crs(3043,inplace=True)
waywidth['geometry'] = waywidth['geometry'].buffer(5) # two tracks requires a roughly 10m wide way.  More including cuttings or embankments
waywidth.to_crs(4326,inplace=True)

In [220]:
#df['element_length'] = df.apply(lambda r:sum([a for a in r['geometry']]),axis=1)

In [221]:
#df['geometry'].distance

In [222]:
def iframe_table(table_entries,width_magic=310,height_per_row_magic=35):
    table_start = """
    <!DOCTYPE html>
    <html>
    <head>

    </head>
    <body>
    
    <table id="t01">
    """

    table_row = """
        <tr>
        <td>{}</td>
        <td>{}</td>
        </tr> """.format

    table_end = """
        </table>
        </body>
        </html>"""
    table_row_list = [table_row(name,value) for name,value in table_entries.items()] 
    table_rows = '\n'.join(table_row_list)
    width, height = width_magic, len(table_row_list)*height_per_row_magic
    return table_start+table_rows+table_end, (width, height)

In [223]:
df

level_0  level_1  objectid name    st_length_  \
0        0        0         1  CS3  65926.744941   
1        0        1         1  CS3  65926.744941   
2        0        2         1  CS3  65926.744941   
3        0        3         1  CS3  65926.744941   
4        1        0         2  CS2  27395.409475   
5        2        0         3  CS1  50417.735543   
6        2        1         3  CS1  50417.735543   

                                            geometry  
0  LINESTRING Z (0.10847 52.14300 0.00000, 0.1067...  
1  LINESTRING Z (0.10847 52.14300 0.00000, 0.1111...  
2  LINESTRING Z (-0.48467 52.14112 0.00000, -0.48...  
3  LINESTRING Z (-0.48422 52.15685 47.99900, -0.4...  
4  LINESTRING Z (-0.73517 51.99543 0.00000, -0.73...  
5  LINESTRING Z (-1.00265 51.92588 0.00000, -0.99...  
6  LINESTRING Z (-1.00266 51.92588 0.00000, -1.01...

In [224]:
columns_to_display = {'name':'Name:','st_length_':'Length:'}
m = folium.Map(control_scale=True)
feature_dict={a:folium.FeatureGroup(name=a) for a in list(df['name'].unique())}
for r in df.iterrows():
    location_tmp = list([(lat, lon) for lon, lat, alt in r[1]['geometry'].coords])
    display_dict = { b:r[1][a] for a,b in columns_to_display.items()}
    iframe_data, box_dimensions = iframe_table(display_dict)
    iframe = folium.IFrame(iframe_data, width=box_dimensions[0], height=box_dimensions[1])
    folium.features.PolyLine(locations=location_tmp, popup=folium.Popup(iframe)).add_to(feature_dict[r[1]['name']])
    wayextentdict = display_dict.copy()
    wayextentdict['Route width']='10m'
    extiframe_data, extbox_dimensions = iframe_table(wayextentdict)
    extiframe = folium.IFrame(extiframe_data, width=extbox_dimensions[0], height=extbox_dimensions[1])
    folium.vector_layers.Polygon(list([(latlon[1], latlon[0]) for latlon in waywidth.loc[r[0]]['geometry'].exterior.coords]), 
                                    opacity=0.8, popup=folium.Popup(extiframe)).add_to(feature_dict[r[1]['name']])
for fgs in feature_dict.values():
    fgs.add_to(m)
#folium.GeoJson(df.to_json(to_wgs84=True)).add_to(m)
folium.LayerControl().add_to(m)
m.fit_bounds(m.get_bounds())
m.save('index.html')

In [225]:
m

In [226]:
columns_to_display = {'Name':'Name:'}
m2 = folium.Map(control_scale=True)
feature_dict2={a:folium.FeatureGroup(name=a) for a in list(bfare['group'].unique())}
for r in bfare.iterrows():
    display_dict = { b:r[1][a] for a,b in columns_to_display.items()}
    iframe_data, box_dimensions = iframe_table(display_dict)
    iframe = folium.IFrame(iframe_data, width=box_dimensions[0], height=box_dimensions[1])
    if r[1]['geometry'].geom_type == 'LineString':
        location_tmp = list([(lat, lon) for lon, lat, alt in r[1]['geometry'].coords])
        folium.features.PolyLine(locations=location_tmp, color=r[1]['color'], popup=folium.Popup(iframe)).add_to(feature_dict2[r[1]['group']])
    elif r[1]['geometry'].geom_type == 'Point':
        location_tmp = list([(lat, lon) for lon, lat, alt in r[1]['geometry'].coords])[0]
        folium.Marker(location=location_tmp, color=r[1]['color'], popup=folium.Popup(iframe)).add_to(feature_dict2[r[1]['group']])
    elif r[1]['geometry'].geom_type == 'Polygon':
        folium.vector_layers.Polygon(list([(latlon[1], latlon[0]) for latlon in r[1]['geometry'].exterior.coords]), 
                                    opacity=0.9, color=r[1]['color'],
                                    fill_color=r[1]['color'],fill_opacity=0.7,
                                    popup=folium.Popup(iframe)).add_to(feature_dict2[r[1]['group']])
for fgs in feature_dict2.values():
         fgs.add_to(m2)
#folium.GeoJson(df.to_json(to_wgs84=True)).add_to(m)
folium.LayerControl().add_to(m2)
m2.fit_bounds(m.get_bounds())
m2.save('bfare.html')

In [227]:
m2

In [228]:
bfare.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich